# Predicting lung cancer survival time by OWKIN

### Problem

- supervised survival prediction problem
- predict the survival time of a patient (remaining days to live) from one three-dimensional CT scan (grayscale image) and a set of pre-extracted quantitative imaging features, as well as clinical data

### Import

In [1]:
import numpy as np
import os
import matplotlib.pyplot as plt
import pandas as pd
from sklearn.preprocessing import LabelEncoder
import autosklearn.regression
import time

# concordance index (C-index)
from metrics_t9gbvr2 import cindex

/home/damien/.local/lib/python3.6/site-packages/sklearn/externals/joblib/__init__.py:15: DeprecationWarning: sklearn.externals.joblib is deprecated in 0.21 and will be removed in 0.23. Please import this functionality directly from joblib, which can be installed with: pip install joblib. If this warning is raised when loading pickled models, you may need to re-serialize those models with scikit-learn 0.21+.
  warnings.warn(msg, category=DeprecationWarning)


### Data

- x_train : data_Q0G7b5t
- y_train : output_VSVxRFU.csv
- x_test : data_9Cbe5hx

In [2]:
data_folder_path = "../data"
training_folder_path = os.path.join(data_folder_path, "data_Q0G7b5t")
test_folder_path = os.path.join(data_folder_path, "data_9Cbe5hx")

training_ct_scan_names = [os.path.join(root,file_name) for root,_,file_names in os.walk(training_folder_path) for file_name in file_names if file_name.endswith('.npz')]
test_ct_scan_names = [os.path.join(root,file_name) for root,_,file_names in os.walk(test_folder_path) for file_name in file_names if file_name.endswith('.npz')]

print("Number of training ct scans : {}".format(len(training_ct_scan_names)))
print("Number of test ct scans : {}".format(len(test_ct_scan_names)))

training_features_path = os.path.join(training_folder_path, "features")
test_features_path = os.path.join(test_folder_path, "features")

submission_file_path = "../random_submission_example"

Number of training ct scans : 300
Number of test ct scans : 125


In [3]:
archive = np.load(training_ct_scan_names[0])
scan = archive['scan']
mask = archive['mask']
# scan.shape equals mask.shape

In [4]:
df_train_output = pd.read_csv(os.path.join(data_folder_path, "output_VSVxRFU.csv"), index_col=0)
p0 = df_train_output.loc[202]
print("p0.Event", p0.Event) # prints 1 or 0
print("p0.SurvivalTime", p0.SurvivalTime)
# prints time to event (time to death or time to last known alive) in days

p0.Event 0
p0.SurvivalTime 1378


In [5]:
df_train_output.sample(5)

SurvivalTime  Event
PatientID                     
53                 1823      0
308                1540      0
212                 441      0
302                 818      0
249                 336      1

### Interpretation

(`1=death observed`, `0=escaped from study`)

### Load training data

In [6]:
file_name = os.path.join(training_features_path, "clinical_data.csv")
df_training_clinical_data = pd.read_csv(file_name, delimiter=',', index_col=0)
print("Nb rows in df_training_clinical_data : {}".format(len(df_training_clinical_data)))

file_name = os.path.join(training_features_path, "radiomics.csv")
df_training_radiomics = pd.read_csv(file_name, delimiter=',', index_col=0, skiprows=[0,2], header=[0])
df_training_radiomics.index.names = ["PatientID"]
print("Nb rows in df_training_radiomics : {}".format(len(df_training_radiomics)))

Nb rows in df_training_clinical_data : 300
Nb rows in df_training_radiomics : 300


### Load test data

In [7]:
file_name = os.path.join(test_features_path, "clinical_data.csv")
df_test_clinical_data = pd.read_csv(file_name, delimiter=',', index_col=0)
print("Nb rows in df_training_clinical_data : {}".format(len(df_test_clinical_data)))

file_name = os.path.join(test_features_path, "radiomics.csv")
df_test_radiomics = pd.read_csv(file_name, delimiter=',', index_col=0 , skiprows=[0,2], header=[0])
df_test_radiomics.index.names = ["PatientID"]
print("Nb rows in df_training_radiomics : {}".format(len(df_test_clinical_data)))

Nb rows in df_training_clinical_data : 125
Nb rows in df_training_radiomics : 125


### clinical_data.csv

In [8]:
df_training_clinical_data.sample(5)

Histology  Mstage  Nstage SourceDataset  Tstage  \
PatientID                                                                  
25                  Adenocarcinoma       0       0            l2       1   
276        squamous cell carcinoma       0       2            l1       2   
380                 Adenocarcinoma       0       0            l2       2   
105                 Adenocarcinoma       0       0            l2       1   
333        Squamous cell carcinoma       0       0            l2       2   

               age  
PatientID           
25         80.0000  
276        66.9733  
380        46.0000  
105        68.0000  
333        80.0000

#### Are there NaN values in df_training_clinical_data ?

In [9]:
#df_training_clinical_data.info()
df_training_clinical_data.isnull().sum()

Histology        20
Mstage            0
Nstage            0
SourceDataset     0
Tstage            0
age              16
dtype: int64

### Remark

There are NaN values in columns Histology and age. We will not use these in our study so no problem.

### radiomics.csv

In [10]:
df_training_radiomics.sample(5)

original_shape_Compactness1  original_shape_Compactness2  \
PatientID                                                             
236                           0.037035                     0.487334   
202                           0.027815                     0.274892   
275                           0.025621                     0.233240   
196                           0.035195                     0.440105   
180                           0.026057                     0.241237   

           original_shape_Maximum3DDiameter  \
PatientID                                     
236                               30.215890   
202                               48.559242   
275                               84.711274   
196                               40.938979   
180                               21.679483   

           original_shape_SphericalDisproportion  original_shape_Sphericity  \
PatientID                                                                     
236                                     1.270743                   0.786941   
202                                     1.537964                   0.650210   
275                                     1.624547                   0.615556   
196                                     1.314664                   0.760651   
180                                     1.606395                   0.622512   

           original_shape_SurfaceArea  original_shape_SurfaceVolumeRatio  \
PatientID                                                                  
236                       2021.209737                           0.338850   
202                       5431.333210                           0.275228   
275                      15755.744224                           0.175430   
196                       4202.893104                           0.247271   
180                       1020.691107                           0.677731   

           original_shape_VoxelVolume  original_firstorder_Energy  \
PatientID                                                           
236                            5992.0                6.100786e+08   
202                           19786.0                3.942944e+09   
275                           89905.0                7.989922e+08   
196                           17037.0                1.809314e+09   
180                            1530.0                1.114320e+08   

           original_firstorder_Entropy  ...  original_glrlm_LongRunEmphasis  \
PatientID                               ...                                   
236                           4.448748  ...                        3.071380   
202                           5.138062  ...                        1.457980   
275                           2.689308  ...                        4.173960   
196                           4.910161  ...                        1.737362   
180                           4.943431  ...                        1.213471   

           original_glrlm_GrayLevelNonUniformity  \
PatientID                                          
236                                   187.661508   
202                                   555.378594   
275                                 10174.890579   
196                                   520.206978   
180                                    57.006841   

           original_glrlm_RunLengthNonUniformity  \
PatientID                                          
236                                  3177.762863   
202                                 14592.303727   
275                                 29857.724341   
196                                 11037.997049   
180                                  1277.346557   

           original_glrlm_RunPercentage  \
PatientID                                 
236                            0.738318   
202                            0.891330   
275                            0.630317   
196                            0.844619   
180                            0.938713   

           original_glrlm_

#### Are there NaN values in df_training_radiomics ?

In [11]:
#df_training_radiomics.info()
df_training_radiomics.isnull().sum().sum()

0

### Remark

There are no NaN values in df_training_radiomics.

### Make sure that PatientID are aligned in df_training_clinical_data and df_training_radiomics

In [12]:
(df_training_clinical_data.index.values==df_training_radiomics.index.values).sum()

300

$300$ means that all PatientIDs are aligned in both training dataframes

### Make sure that PatientID are aligned in df_test_clinical_data and df_test_radiomics

In [13]:
(df_test_clinical_data.index.values==df_test_radiomics.index.values).sum()

125

$125$ means that all PatientIDs are aligned in both test dataframes

### Baseline model for survival regression on NSCLC clinical data : Cox proportional hazard (Cox-PH) model

This baseline is trained on a selection of features from both clinical data file and radiomics file. A Cox-PH model was fitted on

- 1 - Tumor sphericity, a measure of the roundness of the shape of the tumor region relative to a sphere, regardless its dimensions (size).
- 2 - The tumor's surface to volume ratio is a measure of the compactness of the tumor, related to its size.
- 3 - The tumor's maximum 3d diameter The biggest diameter measurable from the tumor volume
- 4 - The dataset of origin
- 5 - The N-tumoral stage grading of the tumor describing nearby (regional) lymph nodes involved
- 6 - The tumor's joint entropy, specifying the randomness in the image pixel values
- 7 - The tumor's inverse different, a measure of the local homogeneity of the tumor
- 8 - The tumor's inverse difference moment is another measurement of the local homogeneity of the tumor

### Name of variables

- 1 - original_shape_Sphericity
- 2 - original_shape_SurfaceVolumeRatio
- 3 - original_shape_Maximum3DDiameter
- 4 - l1 (0) or l2 (1)
- 5 - Nstage
- 6 - original_firstorder_Entropy
- 7 - inverse difference (original_glcm_Id)
- 8 - inverse difference moment (original_glcm_Idm) (according to [here](https://static-content.springer.com/esm/art%3A10.1038%2Fncomms5006/MediaObjects/41467_2014_BFncomms5006_MOESM716_ESM.pdf), ctr+F IDMN and [here](https://github.com/cerr/CERR/wiki/GLCM_global_features))

### Remark

Variables used in the baseline use quantitve and qualitive variables. (dataset of origin (l1 or l2)) makes no sens 

In [14]:
df_training_clinical_data.head(5)

Histology  Mstage  Nstage SourceDataset  Tstage  \
PatientID                                                                  
202                 Adenocarcinoma       0       0            l2       2   
371                     large cell       0       2            l1       4   
246        squamous cell carcinoma       0       3            l1       2   
240                            nos       0       2            l1       3   
284        squamous cell carcinoma       0       3            l1       4   

               age  
PatientID           
202        66.0000  
371        64.5722  
246        66.0452  
240        59.3566  
284        71.0554

### Encode SourceDataset ("dataset of origin") with value between 0 and n_datasets-1.

In [15]:
encoder = LabelEncoder()
encoder.fit(df_training_clinical_data["SourceDataset"])
df_training_clinical_data["SourceDataset"] = encoder.transform(df_training_clinical_data["SourceDataset"])

In [16]:
df_training_clinical_data.head(5)

Histology  Mstage  Nstage  SourceDataset  Tstage  \
PatientID                                                                   
202                 Adenocarcinoma       0       0              1       2   
371                     large cell       0       2              0       4   
246        squamous cell carcinoma       0       3              0       2   
240                            nos       0       2              0       3   
284        squamous cell carcinoma       0       3              0       4   

               age  
PatientID           
202        66.0000  
371        64.5722  
246        66.0452  
240        59.3566  
284        71.0554

In [17]:
df_X_train = pd.concat([df_training_radiomics[["original_shape_Sphericity", 
                       "original_shape_SurfaceVolumeRatio", 
                       "original_shape_Maximum3DDiameter",
                       "original_firstorder_Entropy",
                       "original_glcm_Id",
                       "original_glcm_Idm"]],
                        df_training_clinical_data[["SourceDataset",
                                                  "Nstage"]]
                       ], sort=False, axis=1)

In [18]:
df_X_train = df_X_train.astype(float)
df_X_train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 300 entries, 202 to 366
Data columns (total 8 columns):
original_shape_Sphericity            300 non-null float64
original_shape_SurfaceVolumeRatio    300 non-null float64
original_shape_Maximum3DDiameter     300 non-null float64
original_firstorder_Entropy          300 non-null float64
original_glcm_Id                     300 non-null float64
original_glcm_Idm                    300 non-null float64
SourceDataset                        300 non-null float64
Nstage                               300 non-null float64
dtypes: float64(8)
memory usage: 21.1 KB


### AutoML sklearn

In [19]:
data = {"PatientID" :  df_train_output.index.values,
        "SurvivalTime" : df_train_output["SurvivalTime"].values,
        "Event" :  df_train_output["Event"].values
       }
temp = pd.DataFrame(data)
temp = temp.set_index(["PatientID", "Event"])
temp["SurvivalTime"]

PatientID  Event
202        0        1378
371        1         379
246        1         573
240        0         959
284        0        2119
                    ... 
261        0        1540
298        0         946
129        0         559
273        0        1952
366        0         858
Name: SurvivalTime, Length: 300, dtype: int64

In [20]:
from sklearn.model_selection import ShuffleSplit
from sklearn.model_selection._split import BaseShuffleSplit, _validate_shuffle_split
from sklearn.utils import check_random_state
from sklearn.utils.validation import _num_samples

In [21]:
random_state = 42
test_size = 0.33
n_splits = 1
time_left_for_this_task = 3600 #1200 #60 # in seconds
per_run_time_limit = 30

In [22]:
suffle_split = ShuffleSplit(n_splits=n_splits, test_size=test_size, random_state=random_state)
ind_train, ind_test = [_tuple for _tuple in suffle_split._iter_indices(df_X_train, y=df_train_output["SurvivalTime"], groups=None)][0]
n_train = len(ind_train)
n_test = len(ind_train)

In [23]:
class ShuffleSplit(BaseShuffleSplit):
    """
    Taken from following links
    https://github.com/automl/auto-sklearn/pull/442/files ctr+F Unknown CrossValidator.
    https://github.com/scikit-learn/scikit-learn/blob/master/sklearn/model_selection/_split.py ctrl +F
    """
    
    def __init__(self, n_splits=10, test_size=None, train_size=None,
                 random_state=None):
        n_splits = 1 # !!!!!!!!!!!!!!!!!!!!!!!!!!!!! PROBLEM : n_splits stays at 10 even when changing default value

        super().__init__(
            n_splits=n_splits,
            test_size=test_size,
            train_size=train_size,
            random_state=random_state)
        self._default_test_size = 0.1

    def _iter_indices(self, X, y=None, groups=None):
        n_samples = _num_samples(X)
        n_train, n_test = _validate_shuffle_split(
            n_samples, self.test_size, self.train_size,
            default_test_size=self._default_test_size)

        rng = check_random_state(self.random_state)
        for i in range(self.n_splits):
            # random partition
            permutation = rng.permutation(n_samples)
            ind_test = permutation[:n_test]
            ind_train = permutation[n_test:(n_test + n_train)]
            yield ind_train, ind_test

In [24]:
automl = autosklearn.regression.AutoSklearnRegressor(time_left_for_this_task=time_left_for_this_task, # in seconds
                                                     per_run_time_limit=per_run_time_limit,
                                                     resampling_strategy=ShuffleSplit,
                                                     resampling_strategy_arguments={'n_splits': n_splits,
                                                    'test_size': test_size,
                                                    'random_state': random_state})

def my_cindex(solution, prediction, patient_ids, events, ind_train, ind_test, n_train, n_test):
    prediction = prediction.ravel()
    
    if len(solution)==n_train:
        ind = ind_train
    else:
        ind = ind_test
       
    #print("solution.shape", solution.shape)
    #print("prediction.shape", prediction.shape)
    #print("patient_ids.shape", patient_ids.shape)
    #print("events.shape", events.shape)
    
    #print(autosklearn.metrics.r2(solution, prediction))
    #return autosklearn.metrics.r2(solution, prediction)

    data_solution = {"PatientID" :  patient_ids[ind],
                     "SurvivalTime" : solution,
                     "Event" : events[ind]
                    }
    df_solution = pd.DataFrame(data_solution)
    df_solution = df_solution.set_index("PatientID")
    
    data_prediction = {"PatientID" :  patient_ids[ind],
                       "SurvivalTime" : prediction,
                       "Event" : events[ind]*np.nan # because "`Event`column, whose value does not matter" in metrics_t9gbvr2.py
                      }
    df_prediction = pd.DataFrame(data_prediction)
    df_prediction = df_prediction.set_index("PatientID")
    
    print(cindex(df_solution, df_prediction))
    return cindex(df_solution, df_prediction)

cindex_scorer = autosklearn.metrics.make_scorer(
        name="cindex",
        score_func=my_cindex,
        optimum=1,
        greater_is_better=True,
        needs_proba=False,
        needs_threshold=False,
        patient_ids = df_train_output.index.values,
        events = df_train_output["Event"].values,
        ind_train = ind_train,
        ind_test = ind_test,
        n_train = n_train,
        n_test = n_test
    )

start_time = time.time()
automl.fit(df_X_train.copy(), df_train_output["SurvivalTime"].copy(), dataset_name='data_Q0G7b5t', metric=cindex_scorer) #, metric=cindex_scorer
# Docs for metric in autoML skearln
# https://automl.github.io/auto-sklearn/master/examples/example_metrics.html
# (Metric must be instance of autosklearn.metrics.Scorer.)

#https://automl.github.io/auto-sklearn/master/examples/example_crossvalidation.html
automl.refit(df_X_train.copy(), df_train_output["SurvivalTime"].copy())

execution_time = time.time()-start_time
print("execution_time", execution_time)

# https://automl.github.io/auto-sklearn/master/manual.html
# Cross validation : https://scikit-learn.org/stable/modules/cross_validation.html

/home/damien/.local/lib/python3.6/site-packages/autosklearn/evaluation/train_evaluator.py:197: RuntimeWarning: Mean of empty slice
  Y_train_pred = np.nanmean(Y_train_pred_full, axis=0)


[WARNING] [2020-01-25 15:55:57,364:AutoMLSMBO(1)::data_Q0G7b5t] Could not find meta-data directory /home/damien/.local/lib/python3.6/site-packages/autosklearn/metalearning/files/cindex_regression_dense
0.4999999999986014
[WARNING] [2020-01-25 15:55:57,405:EnsembleBuilder(1):data_Q0G7b5t] No models better than random - using Dummy Score!
0.4999999999986014
[WARNING] [2020-01-25 15:55:57,429:EnsembleBuilder(1):data_Q0G7b5t] No models better than random - using Dummy Score!


/home/damien/.local/lib/python3.6/site-packages/autosklearn/evaluation/train_evaluator.py:197: RuntimeWarning: Mean of empty slice
  Y_train_pred = np.nanmean(Y_train_pred_full, axis=0)


0.6608391608373123
0.8987276154562688
0.6608391608373123
0.6608391608373123


/home/damien/.local/lib/python3.6/site-packages/autosklearn/evaluation/train_evaluator.py:197: RuntimeWarning: Mean of empty slice
  Y_train_pred = np.nanmean(Y_train_pred_full, axis=0)


...

0.7026573426553772
0.6836003770021831


/home/damien/.local/lib/python3.6/site-packages/autosklearn/evaluation/train_evaluator.py:197: RuntimeWarning: Mean of empty slice
  Y_train_pred = np.nanmean(Y_train_pred_full, axis=0)


0.6674125874107205
0.7264373232792398
0.6674125874107205
0.7026573426553772
0.7125874125854194
0.7074125874106086
0.7062937062917307
0.7053146853127125
0.7051748251728527
0.7051748251728527
0.7048951048931332
0.7048951048931332
0.7048951048931332
0.7048951048931332
0.7048951048931332
0.7043356643336942
0.7040559440539746
0.7037762237742552
0.7037762237742552
0.7034965034945357
0.7034965034945357
0.7032167832148162
0.7029370629350967
0.7029370629350967
0.7026573426553772
0.7026573426553772
0.7026573426553772
0.7026573426553772
0.7026573426553772
0.7026573426553772
0.7023776223756577
0.7023776223756577
0.7023776223756577
0.7023776223756577
0.7020979020959383
0.7020979020959383
0.7018181818162187
0.7018181818162187
0.7018181818162187
0.7015384615364992
0.7015384615364992
0.7015384615364992
0.7015384615364992
0.7015384615364992
0.7015384615364992
0.7015384615364992
0.7012587412567797
0.7012587412567797
0.7012587412567797
0.7012587412567797
0.7009790209770602
0.7009790209770602
0.7009790209

0.7264335664315344
0.7272727272706929
0.7275524475504125
0.7278321678301319
0.726153846151815
0.726153846151815
0.7264335664315344
0.7286713286692904
0.7269930069909735
0.7281118881098515
0.7281118881098515
0.7281118881098515
0.7264335664315344
0.7253146853126565
0.7264335664315344
0.725594405592376
0.7303496503476075
0.7309090909070465
0.7269930069909735
0.7275524475504125
0.7275524475504125
0.7275524475504125
0.7272727272706929
0.7272727272706929
0.7272727272706929
0.7272727272706929
0.7272727272706929
0.726713286711254
0.7264335664315344
0.7264335664315344
0.7264335664315344
0.7269930069909735
0.726153846151815
0.7269930069909735
0.726713286711254
0.726713286711254
0.7272727272706929
0.7241958041937785
0.7272727272706929
0.726713286711254
0.725594405592376
0.7286713286692904
0.7272727272706929
0.7264335664315344
0.726153846151815
0.7258741258720954
0.7286713286692904
0.7247552447532175
0.7269930069909735
0.726713286711254
0.726153846151815
0.7272727272706929
0.7269930069909735
0.727

[16:55:53] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
execution_time 3599.478259086609


In [25]:
automl.resampling_strategy.__name__

'ShuffleSplit'

In [26]:
print(np.c_[automl.cv_results_["status"], automl.cv_results_["mean_test_score"]])

[['Success' '0.6608391608373123']
 ['Success' '0.6646153846135255']
 ['Success' '0.5731468531452499']
 ...
 ['Success' '0.5949650349633707']
 ['Success' '0.7026573426553772']
 ['Success' '0.6674125874107205']]


In [27]:
print("{:0.2f}".format(automl.cv_results_["mean_test_score"].max()))
print()
print(automl.sprint_statistics())
#automl._automl[0]._metric.name

0.71

auto-sklearn results:
  Dataset name: data_Q0G7b5t
  Metric: cindex
  Best validation score: 0.712587
  Number of target algorithm runs: 528
  Number of successful target algorithm runs: 495
  Number of crashed target algorithm runs: 1
  Number of target algorithms that exceeded the time limit: 32
  Number of target algorithms that exceeded the memory limit: 0



In [28]:
all_information = automl.get_models_with_weights()
index_regressor = 5
weights = []
print("Models used with corresponding weights :\n")
for weight, simple_regression_pipeline in all_information:
    print(str(weight)+" : "+simple_regression_pipeline[index_regressor].choice.__class__.__name__)
    weights.append(weight)
print()
print("sum(weights) = ", np.round(sum(weights),2))

Models used with corresponding weights :

0.7 : LibLinear_SVR
0.16 : KNearestNeighborsRegressor
0.06 : XGradientBoostingRegressor
0.04 : GradientBoosting
0.02 : LibSVM_SVR
0.02 : RidgeRegression

sum(weights) =  1.0


### Test

In [29]:
df_test_clinical_data["SourceDataset"] = encoder.transform(df_test_clinical_data["SourceDataset"])

In [30]:
df_X_test = pd.concat([df_test_radiomics[["original_shape_Sphericity", 
                       "original_shape_SurfaceVolumeRatio", 
                       "original_shape_Maximum3DDiameter",
                       "original_firstorder_Entropy",
                       "original_glcm_Id",
                       "original_glcm_Idm"]],
                        df_test_clinical_data[["SourceDataset",
                                                  "Nstage"]]
                       ], sort=False, axis=1)

In [31]:
df_X_test = df_X_test.astype(float)
df_X_test.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 125 entries, 13 to 274
Data columns (total 8 columns):
original_shape_Sphericity            125 non-null float64
original_shape_SurfaceVolumeRatio    125 non-null float64
original_shape_Maximum3DDiameter     125 non-null float64
original_firstorder_Entropy          125 non-null float64
original_glcm_Id                     125 non-null float64
original_glcm_Idm                    125 non-null float64
SourceDataset                        125 non-null float64
Nstage                               125 non-null float64
dtypes: float64(8)
memory usage: 8.8 KB


In [32]:
y_hat = automl.predict(df_X_test)

In [33]:
df_predicted_survival_time = pd.read_csv(os.path.join(submission_file_path, "random_submission_0vhlEZN.csv"), index_col=0)
df_predicted_survival_time.head(5)

SurvivalTime  Event
PatientID                     
13           788.417673    NaN
155          427.650092    NaN
404          173.587222    NaN
407          389.877973    NaN
9           1580.767244    NaN

In [34]:
df_predicted_survival_time.index = df_test_clinical_data.index
df_predicted_survival_time["SurvivalTime"] = y_hat

In [35]:
df_predicted_survival_time.head(5)

SurvivalTime  Event
PatientID                     
13           528.622691    NaN
155         1358.608669    NaN
404          523.066431    NaN
407          706.512898    NaN
9            899.507969    NaN

## $\color{red}{\text{To be continued}}$

### Annexe (just to check detail on training data)

In [36]:
y_hat = automl.predict(df_X_train)

df_hat = df_train_output.copy()
df_hat["SurvivalTime"] = y_hat
df_hat["Event"] = np.nan
cindex(df_train_output , df_hat)

0.6886231333837356